In [1]:
import sympy as sp
import matplotlib.pyplot as plt
import numpy as np
import plotly.graph_objects as go

%matplotlib inline
from numpy import *
d2r = np.deg2rad
r2d = np.degrees

In [2]:
from sympy.physics.vector import init_vprinting
init_vprinting(use_latex='mathjax', pretty_print=False)

In [3]:
from sympy.physics.mechanics import dynamicsymbols

### Parámetros DH

In [4]:
theta, alpha, a, d = dynamicsymbols('theta alpha a d')
theta, alpha, a, d 

(theta, alpha, a, d)

### Parámetros del robot

In [5]:
theta1, theta2, theta3, d1 = dynamicsymbols('theta1 theta2 theta3 d1')
theta1, theta2, theta3

(theta1, theta2, theta3)

In [6]:
rot = sp.Matrix([[sp.cos(theta), -sp.sin(theta)*sp.cos(alpha), sp.sin(theta)*sp.sin(alpha)],
                 [sp.sin(theta), sp.cos(theta)*sp.cos(alpha), -sp.cos(theta)*sp.sin(alpha)],
                 [0, sp.sin(alpha), sp.cos(alpha)]])

trans = sp.Matrix([a*sp.cos(theta),a*sp.sin(theta),d])

last_row = sp.Matrix([[0, 0, 0, 1]])

m = sp.Matrix.vstack(sp.Matrix.hstack(rot, trans), last_row)
m

Matrix([
[cos(theta), -sin(theta)*cos(alpha),  sin(alpha)*sin(theta), a*cos(theta)],
[sin(theta),  cos(alpha)*cos(theta), -sin(alpha)*cos(theta), a*sin(theta)],
[         0,             sin(alpha),             cos(alpha),            d],
[         0,                      0,                      0,            1]])

In [7]:
l1 = 0.2
l2 = 0.5
L1 = 0.7

In [12]:
m01 = m.subs({theta:theta1, d:0.2, a:0, alpha:pi/2})
m12 = m.subs({theta:theta2, d:0, a:0.7, alpha:-pi/2})
m23 = m.subs({theta:0, d:d1, a:0, alpha:0})

m03 = (m01*m12*m23)
mtcp = sp.simplify(m03)
px = mtcp[0,3]
py = mtcp[1,3]
pz = mtcp[2,3]
fx = sp.lambdify((theta1, theta2, d1), px, 'numpy')
fy = sp.lambdify((theta1, theta2, d1), py, 'numpy')
fz = sp.lambdify((theta1, theta2, d1), pz, 'numpy')

In [13]:
mtcp

Matrix([
[-6.12323399573677e-17*sin(theta1)*sin(theta2) + cos(theta1)*cos(theta2), -3.74939945665464e-33*sin(theta1)*cos(theta2) - 1.0*sin(theta1) - 6.12323399573677e-17*sin(theta2)*cos(theta1), -6.12323399573677e-17*sin(theta1)*cos(theta2) + 6.12323399573677e-17*sin(theta1) - 1.0*sin(theta2)*cos(theta1), -(6.12323399573677e-17*sin(theta1)*cos(theta2) - 6.12323399573677e-17*sin(theta1) + 1.0*sin(theta2)*cos(theta1))*d1 - 4.28626379701574e-17*sin(theta1)*sin(theta2) + 0.7*cos(theta1)*cos(theta2)],
[ sin(theta1)*cos(theta2) + 6.12323399573677e-17*sin(theta2)*cos(theta1), -6.12323399573677e-17*sin(theta1)*sin(theta2) + 3.74939945665464e-33*cos(theta1)*cos(theta2) + 1.0*cos(theta1), -1.0*sin(theta1)*sin(theta2) + 6.12323399573677e-17*cos(theta1)*cos(theta2) - 6.12323399573677e-17*cos(theta1), -(1.0*sin(theta1)*sin(theta2) - 6.12323399573677e-17*cos(theta1)*cos(theta2) + 6.12323399573677e-17*cos(theta1))*d1 + 0.7*sin(theta1)*cos(theta2) + 4.28626379701574e-17*sin(theta2)*cos(theta1)],
[    

### Ploteo del área del trabajo del robot

In [17]:
n_theta = 40
d_n = 20

theta1s = np.linspace(d2r(0), d2r(30), n_theta) # desired range of motion for joint 1
theta2s = np.linspace(d2r(75), d2r(105), n_theta) # desired range of motion for joint 2
d3s = np.linspace(0.0, -0.4, d_n) 
#theta3s = np.linspace(d2r(0), d2r(25), n_theta) # desired range of motion for joint 3
#d3s = np.linspace(0, 1, d_n) 
# theta2s = np.linspace(d2r(0), d2r(360)) # desired range of motion for joint 2
total = len(theta1s)*len(theta2s)
print(total)

posx = []
posy = []
posz = []

counter = 0

for t1 in theta1s:
    for t2 in theta2s:
        for d3 in d3s:
            x = float(fx(t1, t2, d3))
            y = float(fy(t1, t2, d3))
            z = float(fz(t1, t2, d3))
            posx.append(x)
            posy.append(y)
            posz.append(z)
#                 y = fy(l1,l2,theta1,theta2)
x = np.array(posx)
y = np.array(posy)
z = np.array(posz)

'''
fig = go.Figure(data=go.Scatter3d(
    x=x, y=y, z=z,
    marker=dict(
        size=4,
        color=z,
        colorscale='Viridis',
    ),
    line=dict(
        color='darkblue',
        width=2
    )
))

'''
data = go.Scatter3d(
    x=x, 
    y=y, 
    z=z,
    mode='markers', 
    opacity=0.025,  
    marker=dict(
        size=4,
        color=z,
        colorscale='Viridis',
        line=dict(
            color='rgb(0, 0, 0)',
            width=1
        )
    ))

layout = go.Layout(
    scene = go.layout.Scene(
    aspectmode='manual',
    aspectratio=go.layout.scene.Aspectratio(
        x=1, y=1, z=1
    ))
)

fig = go.Figure(data=data, layout=layout)
'''
fig.add_trace(go.Scatter3d(
     x=[x_target], 
     y=[y_target], 
     z=[z_target],
     mode='markers', 
     marker=dict(
         symbol='x',
         size=5,
         color='rgb(255,255,255)'
     )))
'''
fig.show()

1600


In [22]:
target_param = [d2r(25.0), d2r(85.0), -0.2]
target = f(target_param)
x_target = target[0]
y_target = target[1]
z_target = target[2]
print(target)
# Obtener punto valuando los parámetros

[0.23586475 0.10998554 0.87990514]


In [23]:
def f(param):
    p0 = param[0]
    p1 = param[1]
    p2 = param[2]
    
    point = []
    point = ([fx(p0, p1, p2),
              fy(p0, p1, p2),
              fz(p0, p1, p2)])
    
    return np.array(point)

# Distancia euclidiana
def distance(p1, p2):
    dist = np.linalg.norm(p1-p2)
    return dist

In [24]:
%%time

n_theta = 36
d_n = 20

params = []

theta1s = np.linspace(d2r(0), d2r(30), n_theta) # desired range of motion for joint 1
theta2s = np.linspace(d2r(75), d2r(105), n_theta) # desired range of motion for joint 2
d3s = np.linspace(0.0, -0.4, d_n)
total = len(theta1s)*len(theta2s)*len(d3s)
print(total)

for theta1 in theta1s:
        for theta2 in theta2s:
            for d3 in d3s:
                params.append([theta1, theta2, d3])

params = np.array(params)
np.random.shuffle(params)

actual_err = 100
required_err = 0.01

counter = 0

points = []

for param in params:
    points.append(f(param))
    new_err = distance(f(param), target)
    counter += 1
    if new_err<actual_err:
        actual_err = new_err
        best_param = param
    if new_err<required_err:
        break

25920
CPU times: user 161 ms, sys: 3.19 ms, total: 164 ms
Wall time: 163 ms


In [25]:
# Setear mejores puntos para el ploteo
best = f(best_param)
x_best = best[0]
y_best = best[1]
z_best = best[2]

points = np.array(points)

print(counter)
print('error actual:', actual_err)
print('parametros:', r2d(best_param))
print('target:', target)
print('achieved:',f(best_param))

180
error actual: 0.00783332148964414
parametros: [ 25.71428571  85.28571429 -12.06226937]
target: [0.23586475 0.10998554 0.87990514]
achieved: [0.24086951 0.11599664 0.88032932]
